# Set up

In [ ]:
!pip install transformers[torch]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 35.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.0/302.0 kB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 35.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 34.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.1/258.1 kB 21.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 295.0/295.0 kB 16.2 MB/s eta 0:00:00


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
import pandas as pd
import json
import torch
from transformers import BertTokenizer, BertForTokenClassification, DataCollatorForTokenClassification, Trainer, TrainingArguments
from torch.utils.data import DataLoader, Dataset, random_split
# from tqdm import tqdm
import re
from nltk.tokenize import sent_tokenize
import spacy
from sklearn.metrics import mean_squared_error

# Data Processing - csv

In [180]:
train = pd.read_csv('drive/My Drive/train.csv')
test = pd.read_csv('drive/My Drive/test.csv')
val = pd.read_csv('drive/My Drive/val.csv')

In [181]:
# Fill in missing pmid in csv
train.at[622, 'pmid'] = '19957776'

In [182]:
# Cannot set as int for 'PMC3872591'
train['pmid'] = train['pmid'].astype(str)
test['pmid'] = test['pmid'].astype(str)
val['pmid'] = val['pmid'].astype(str)

In [183]:
data = pd.concat([train, test, val], axis=0)
data = data.reset_index(drop=True)

Empty DataFrame
Columns: [question, pmid, input_text, target_text, Adaptation_Version, Question_Type]
Index: []

In [184]:
data

question      pmid                                         input_text  \
0           1  29857264  Exercise-Associated Muscle Cramps (EAMC) are a...   
1           1  33722257  Background: Muscle cramp is a painful, involun...   
2           1  31696455  Muscle cramp is a temporary but intense and pa...   
3           1  30168894  Muscular cramp is a common symptom in healthy ...   
4           1  29763070  Muscle cramps result in continuous, involuntar...   
..        ...       ...                                                ...   
916        66  35102405  Nephrotic syndrome (NS) encompasses a variety ...   
917        66  35017338  Children with nephrotic syndrome (NS) have a n...   
918        66  34979093  Background: Although venous thromboembolism is...   
919        66  34839817  Background: Steroid resistant nephrotic syndro...   
920        66  34775776  Chylothorax is an uncommon and serious clinica...   

                                           target_text  Adaptation_Version  \
0    Exercise-Associated Muscle Cramps (EAMC) are a...                   2   
1    Muscle cramps are unconscious contractions of ...                   2   
2    Muscle cramp is a temporary but intense, painf...                   2   
3    Muscle cramps are common in healthy people, es...                   2   
4    Muscle cramps cause constant and unintended co...                   2   
..                                                 ...                 ...   
916  Nephrotic syndrome (NS) includes a variety of ...                   2   
917  Nephrotic Syndrome (NS) is a combination of ki...                   2   
918  Blood clots are a well-known problem associate...                   2   
919  Steroid Resistant Nephrotic Syndrome (SRNS) is...                   2   
920  Chylothorax is an uncommon and serious medical...                   2   

    Question_Type  
0               C  
1               C  
2               C  
3               C  
4               C  
..            ...  
916             B  
917             B  
918             B  
919             B  
920             B  

[921 rows x 6 columns]

In [185]:
data[data['pmid'] == '33347023']

# dup pmid - 2 adaptations
# !!!version_id unable to map

question      pmid                                         input_text  \
791         2  33347023  Purpose: Several studies have previously repor...   
792         2  33347023  Purpose: Several studies have previously repor...   

                                           target_text  Adaptation_Version  \
791  Dry eye, depression, and treatent of depressio...                   2   
792  Studies show that there is a link between depr...                   2   

    Question_Type  
791             B  
792             B

# Data Processing - json

In [186]:
file_path = 'drive/My Drive/data.json'
with open(file_path, 'r') as file:
    dj = json.load(file)

In [187]:
dj

{'1': {'15902691': {'Title': 'Muscle cramps',
   'abstract': {'1': 'Muscle cramps are a common problem characterized by a sudden, painful, involuntary contraction of muscle.',
    '2': 'These true cramps, which originate from peripheral nerves, may be distinguished from other muscle pain or spasm.',
    '3': 'Medical history, physical examination, and a limited laboratory screen help to determine the various causes of muscle cramps.',
    '4': 'Despite the "benign" nature of cramps, many patients find the symptom very uncomfortable.',
    '5': 'Treatment options are guided both by experience and by a limited number of therapeutic trials.',
    '6': 'Quinine sulfate is an effective medication, but the side-effect profile is worrisome, and other membrane-stabilizing drugs are probably just as effective.',
    '7': 'Patients will benefit from further studies to better define the pathophysiology of muscle cramps and to find more effective medications with fewer side-effects.'},
   'adaptat

In [188]:
question_list = []

for question_id, question in dj.items():
    row = {
        'QID': question_id,
        'Question': question['question'],
        'Question_Type': question['question_type']
    }

    question_list.append(row)

df_q = pd.DataFrame(question_list)

In [189]:
df_q

# 75 questions

QID                                           Question Question_Type
0    1                          What causes muscle spasm?             C
1    2                           What does duloxetine do?             B
2    3              How can i reduce my potassium levels?             C
3    4                         How is diabetes diagnosed?             C
4    5                        How to treat a bakers cyst?             C
..  ..                                                ...           ...
70  71  What happens in the body to cause achondroplasia?             B
71  72  What is newborn metabolic screening? what can ...             C
72  73  In adult patients with total hip replacements ...             C
73  74  Why do i have to constantly clear my throat an...             C
74  75     What is a gene affected by sickle cell anemia?             B

[75 rows x 3 columns]

In [ ]:
# dj_list = []

# for question_id, question in dj.items():
#   for pmid, text_data in question.items():
#     if isinstance(text_data, dict):
#       row = {
#         'QID': question_id,
#         'Question': question['question'],
#         'Question_Type': question['question_type'],
#         'pmid': pmid,
#         'Title': text_data.get('Title', None),
#       }

#       abstract = text_data.get('abstract', {})
#       adaptations = text_data.get('adaptations', {})

#       for sentence, text in abstract.items():
#         row[f'Abstract_{sentence}'] = text

#       for adaptation_id, adaptation_text in adaptations.items():
#         row[f'Adaptation_{adaptation_id}'] = adaptation_text

#       dj_list.append(row)

# df_a = pd.DataFrame(dj_list)

In [ ]:
# df_a

# 749 abstracts ??? vs 750

QID                                        Question Question_Type  \
0     1                       What causes muscle spasm?             C   
1     1                       What causes muscle spasm?             C   
2     1                       What causes muscle spasm?             C   
3     1                       What causes muscle spasm?             C   
4     1                       What causes muscle spasm?             C   
..   ..                                             ...           ...   
744  75  What is a gene affected by sickle cell anemia?             B   
745  75  What is a gene affected by sickle cell anemia?             B   
746  75  What is a gene affected by sickle cell anemia?             B   
747  75  What is a gene affected by sickle cell anemia?             B   
748  75  What is a gene affected by sickle cell anemia?             B   

         pmid                                              Title  \
0    15902691                                      Muscle cramps   
1    25432724                Diagnosis and treatment of dystonia   
2    29763070                                      Muscle Cramps   
3    29857264  Muscle cramps: A comparison of the two-leading...   
4    30168894              Muscular cramp: causes and management   
..        ...                                                ...   
744  31322815  Combined and differential effects of alpha-tha...   
745  32447424  Functional polymorphisms of BCL11A and HBS1L-M...   
746  32772141  Association between BCL11A, HSB1L-MYB, and Xmn...   
747  33072979  Sickle Cell Disease-Genetics, Pathophysiology,...   
748  33216016  HbF-promoting polymorphisms may specifically r...   

                                            Abstract_1  \
0    Muscle cramps are a common problem characteriz...   
1    The dystonias are a group of disorders charact...   
2    Muscle cramps result in continuous, involuntar...   
3    Exercise-Associated Muscle Cramps (EAMC) are a...   
4    Muscular cramp is a common symptom in healthy ...   
..                                                 ...   
744  Background: Our objective was to investigate t...   
745  Fetal hemoglobin (HbF) ameliorates clinical se...   
746  Sickle cell disease (SCD) is a monogenic disea...   
747  Sickle cell disease (SCD) is a monogenetic dis...   
748  Sickle cell anemia (SCA) is a disease characte...   

                                            Abstract_2  \
0    These true cramps, which originate from periph...   
1    A careful assessment of the clinical manifesta...   
2    Generally, the cramp can last from minutes to ...   
3    Despite scientists tried to understand the phy...   
4    It is prominent in a number of benign neurolog...   
..                                                 ...   
744  Procedure: Steady-state biological parameters ...   
745  The major loci regulating HbF levels are HBB c...   
746  Inter-individual variability in hemoglobin F (...   
747  Phenotypic variation in the clinical presentat...   
748  Because of their effects on HbS polymerization...   

                                            Abstract_3  \
0    Medical history, physical examination, and a l...   
1    If a cause is identified, specific etiology-ba...   
2    Palpating the muscle area of the cramp will pr...   
3    From 1900 to nowadays, the scientific world re...   
4    It is a particular feature of chronic neurogen...   
..                                                 ...   
744  The age of the first hospitalized VOC was also...   
745  However, the impact of noncoding single-nucleo...   
746  HbF levels are affected by, among other factor...   
747  Understanding the pathogenesis and pathophysio...   
748  The aim of our study was to determine if the n...   

                                            Abstract_4  \
0    Despite the "benign" nature of cramps, many pa...   
1    In most cases, a specific cause cannot be iden...   
2    Exercise-associated muscle cramps are th

In [ ]:
# df_a.columns

Index(['QID', 'Question', 'Question_Type', 'pmid', 'Title', 'Abstract_1',
       'Abstract_2', 'Abstract_3', 'Abstract_4', 'Abstract_5', 'Abstract_6',
       'Abstract_7', 'Adaptation_adaptation2', 'Abstract_8', 'Abstract_9',
       'Abstract_10', 'Abstract_11', 'Abstract_12', 'Abstract_13',
       'Abstract_14', 'Abstract_15', 'Abstract_16', 'Abstract_17',
       'Abstract_18', 'Adaptation_adaptation3', 'Abstract_19', 'Abstract_20',
       'Abstract_21', 'Adaptation_adaptation1', 'Abstract_22', 'Abstract_23',
       'Abstract_24', 'Abstract_25', 'Abstract_26', 'Abstract_27',
       'Abstract_28', 'Abstract_29', 'Abstract_30', 'Abstract_31',
       'Abstract_32', 'Abstract_33', 'Abstract_34'],
      dtype='object')

In [ ]:
# df_j
# df_t

Abstract_sentence_id                                           Abstract  \
0                      7  Patients will benefit from further studies to ...   
1                      6  A substantial reduction in symptoms and improv...   
2                      7  A cramp is almost never a local effect but inv...   
3                     11  In conclusion, from the latest investigations ...   
4                      6  Current treatment options are correspondingly ...   
..                   ...                                                ...   
744                   10  They should be studied and interpreted togethe...   
745                   13  Higher HbF concentration may underlie this eff...   
746                   11  Discovery of the molecular mechanisms controll...   
747                    8  We also provide an overview of emerging therap...   
748                    5  We also showed that more HbF-QTL may provide a...   

    Adaptation_sentence_id                                         Adaptation  
0                        7  More studies are needed to better define the e...  
1                        6  A noticeable decrease in symptoms and improved...  
2                        7  A cramp can almost never be explained just by ...  
3                       11  In summary, the signal causing muscles to cont...  
4                        6                      Current treatment is limited.  
..                     ...                                                ...  
744                     10  These genes and their mutations should be stud...  
745                     13  Higher HbF levels may be the cause of this eff...  
746                     11  If researchers could discover the underlying c...  
747                      8  This paper also discusses new therapies for Si...  
748                      5  We also showed that more HbF-QTL may protect m...  

[749 rows x 4 columns]

In [ ]:
# df_merge = pd.concat([df_j, df_t], axis=1)
# df_merge

QID                                        Question Question_Type  \
0     1                       What causes muscle spasm?             C   
1     1                       What causes muscle spasm?             C   
2     1                       What causes muscle spasm?             C   
3     1                       What causes muscle spasm?             C   
4     1                       What causes muscle spasm?             C   
..   ..                                             ...           ...   
744  75  What is a gene affected by sickle cell anemia?             B   
745  75  What is a gene affected by sickle cell anemia?             B   
746  75  What is a gene affected by sickle cell anemia?             B   
747  75  What is a gene affected by sickle cell anemia?             B   
748  75  What is a gene affected by sickle cell anemia?             B   

         pmid                                              Title  \
0    15902691                                      Muscle cramps   
1    25432724                Diagnosis and treatment of dystonia   
2    29763070                                      Muscle Cramps   
3    29857264  Muscle cramps: A comparison of the two-leading...   
4    30168894              Muscular cramp: causes and management   
..        ...                                                ...   
744  31322815  Combined and differential effects of alpha-tha...   
745  32447424  Functional polymorphisms of BCL11A and HBS1L-M...   
746  32772141  Association between BCL11A, HSB1L-MYB, and Xmn...   
747  33072979  Sickle Cell Disease-Genetics, Pathophysiology,...   
748  33216016  HbF-promoting polymorphisms may specifically r...   

    adaptation_id Abstract_sentence_id  \
0     adaptation2                    7   
1     adaptation2                    6   
2     adaptation2                    7   
3     adaptation2                   11   
4     adaptation2                    6   
..            ...                  ...   
744   adaptation3                   10   
745   adaptation3                   13   
746   adaptation3                   11   
747   adaptation3                    8   
748   adaptation3                    5   

                                              Abstract Adaptation_sentence_id  \
0    Patients will benefit from further studies to ...                      7   
1    A substantial reduction in symptoms and improv...                      6   
2    A cramp is almost never a local effect but inv...                      7   
3    In conclusion, from the latest investigations ...                     11   
4    Current treatment options are correspondingly ...                      6   
..                                                 ...                    ...   
744  They should be studied and interpreted togethe...                     10   
745  Higher HbF concentration may underlie this eff...                     13   
746  Discovery of the molecular mechanisms controll...                     11   
747  We also provide an overview of emerging therap...                      8   
748  We also showed that more HbF-QTL may provide a...                      5   

                                            Adaptation  
0    More studies are needed to better define the e...  
1    A noticeable decrease in symptoms and improved...  
2    A cramp can almost never be explained just by ...  
3    In summary, the signal causing muscles to cont...  
4                        Current treatment is limited.  
..                                                 ...  
744  These genes and their mutations should be stud...  
745  Higher HbF levels may be the cause of this eff...  
746  If researchers could discover the underlying c...  
747  This paper also discusses new therapies for Si...  
748  We also showed that more HbF-QTL may protect m...  

[749 rows x 10 columns]

In [190]:
dj_list = []
io_list = []

a_list = []
p_list = []

for question_id, question in dj.items():
  for pmid, text_data in question.items():
    if isinstance(text_data, dict):


      abstract = text_data.get('abstract', {})
      adaptations = text_data.get('adaptations', {})

      for adaptation_id, adaptation in adaptations.items():
        summary = {
          'QID': question_id,
          'Question': question['question'],
          'Question_Type': question['question_type'],
          'pmid': pmid,
          'Title': text_data.get('Title', None),
          'adaptation_id': int(adaptation_id[10:]),
          'abstract_len': len(abstract)
        }
        pi = ''
        po = ''

        for  text_input, text_output in zip(abstract.items(), adaptation.items()):

          text = {
            'Abstract_sentence_id': text_input[0],
            'Abstract': text_input[1],
            'Adaptation_sentence_id': text_output[0],
            'Adaptation': text_output[1]
          }

          dj_list.append(summary)
          io_list.append(text)

          pi += text_input[1]
          po += text_output[1]


        paragraph = {
            'input_paragraph': pi,
            'output_paragraph': po
        }
        a_list.append(summary)
        p_list.append(paragraph)

df_j = pd.DataFrame(dj_list)
df_t = pd.DataFrame(io_list)


df_s = pd.DataFrame(a_list)
df_p = pd.DataFrame(p_list)

In [191]:
df_t

Abstract_sentence_id                                           Abstract  \
0                       1  Muscle cramps are a common problem characteriz...   
1                       2  These true cramps, which originate from periph...   
2                       3  Medical history, physical examination, and a l...   
3                       4  Despite the "benign" nature of cramps, many pa...   
4                       5  Treatment options are guided both by experienc...   
...                   ...                                                ...   
9313                    1  Sickle cell anemia (SCA) is a disease characte...   
9314                    2  Because of their effects on HbS polymerization...   
9315                    3  The aim of our study was to determine if the n...   
9316                    4  Our results confirmed that alpha-thalassemia p...   
9317                    5  We also showed that more HbF-QTL may provide a...   

     Adaptation_sentence_id                                         Adaptation  
0                         1  Muscle cramps are a common problem represented...  
1                         2  These true cramps, coming from nerves outside ...  
2                         3  Medical history, physical check-up, and lab sc...  
3                         4  Despite their harmless nature, cramps are unco...  
4                         5  Experience and limited medical studies guide t...  
...                     ...                                                ...  
9313                      1  Sickle Cell Anemia (SCA) is a genetic blood di...  
9314                      2  Due to their effects on sickle hemoglobin (HbS...  
9315                      3  The aim of our study was to find out if the nu...  
9316                      4  Results showed that alpha-thalassemia protecte...  
9317                      5  We also showed that more HbF-QTL may protect m...  

[9318 rows x 4 columns]

In [192]:
df_jsent = pd.concat([df_j, df_t], axis=1)
df_jsent

QID                                        Question Question_Type  \
0      1                       What causes muscle spasm?             C   
1      1                       What causes muscle spasm?             C   
2      1                       What causes muscle spasm?             C   
3      1                       What causes muscle spasm?             C   
4      1                       What causes muscle spasm?             C   
...   ..                                             ...           ...   
9313  75  What is a gene affected by sickle cell anemia?             B   
9314  75  What is a gene affected by sickle cell anemia?             B   
9315  75  What is a gene affected by sickle cell anemia?             B   
9316  75  What is a gene affected by sickle cell anemia?             B   
9317  75  What is a gene affected by sickle cell anemia?             B   

          pmid                                              Title  \
0     15902691                                      Muscle cramps   
1     15902691                                      Muscle cramps   
2     15902691                                      Muscle cramps   
3     15902691                                      Muscle cramps   
4     15902691                                      Muscle cramps   
...        ...                                                ...   
9313  33216016  HbF-promoting polymorphisms may specifically r...   
9314  33216016  HbF-promoting polymorphisms may specifically r...   
9315  33216016  HbF-promoting polymorphisms may specifically r...   
9316  33216016  HbF-promoting polymorphisms may specifically r...   
9317  33216016  HbF-promoting polymorphisms may specifically r...   

      adaptation_id  abstract_len Abstract_sentence_id  \
0                 2             7                    1   
1                 2             7                    2   
2                 2             7                    3   
3                 2             7                    4   
4                 2             7                    5   
...             ...           ...                  ...   
9313              3             5                    1   
9314              3             5                    2   
9315              3             5                    3   
9316              3             5                    4   
9317              3             5                    5   

                                               Abstract  \
0     Muscle cramps are a common problem characteriz...   
1     These true cramps, which originate from periph...   
2     Medical history, physical examination, and a l...   
3     Despite the "benign" nature of cramps, many pa...   
4     Treatment options are guided both by experienc...   
...                                                 ...   
9313  Sickle cell anemia (SCA) is a disease characte...   
9314  Because of their effects on HbS polymerization...   
9315  The aim of our study was to determine if the n...   
9316  Our results confirmed that alpha-thalassemia p...   
9317  We also showed that more HbF-QTL may provide a...   

     Adaptation_sentence_id                                         Adaptation  
0                         1  Muscle cramps are a common problem represented...  
1                         2  These true cramps, coming from nerves outside ...  
2                         3  Medical history, physical check-up, and lab sc...  
3                         4  Despite their harmless nature, cramps are unco...  
4                         5  Experience and limited medical studies guide t...  
...                     ...                                                ...  
9313                      1  Sickle Cell Anemia (SCA) is a genetic blood di...  
9314                      2  Due to their effects on sickle hemoglobin (HbS...  
9315                      3  The aim of our study was to find out if the nu...  
9316                      4  Results showed that alpha-thalassemia prot

In [193]:
df_jsent.to_csv('json_sent.csv', index=False)

In [194]:
df_p

input_paragraph  \
0    Muscle cramps are a common problem characteriz...   
1    The dystonias are a group of disorders charact...   
2    Muscle cramps result in continuous, involuntar...   
3    Exercise-Associated Muscle Cramps (EAMC) are a...   
4    Muscular cramp is a common symptom in healthy ...   
..                                                 ...   
914  Background: Our objective was to investigate t...   
915  Fetal hemoglobin (HbF) ameliorates clinical se...   
916  Sickle cell disease (SCD) is a monogenic disea...   
917  Sickle cell disease (SCD) is a monogenetic dis...   
918  Sickle cell anemia (SCA) is a disease characte...   

                                      output_paragraph  
0    Muscle cramps are a common problem represented...  
1    Dystonias are disorders with a lot of uncontro...  
2    Muscle cramps cause constant and unintended co...  
3    Exercise-Associated Muscle Cramps (EAMC) are a...  
4    Muscle cramps are common in healthy people, es...  
..                                                 ...  
914  Researchers analyzed the effects of an alpha-t...  
915  Fetal hemoglobin (HbF) makes the severity of S...  
916  Sickle Cell Disease (SCD) is a genetic blood d...  
917  Sickle Cell Disease (SCD) is a genetic disorde...  
918  Sickle Cell Anemia (SCA) is a genetic blood di...  

[919 rows x 2 columns]

In [195]:
df_jpara = pd.concat([df_s, df_p], axis=1)
df_jpara

QID                                        Question Question_Type  \
0     1                       What causes muscle spasm?             C   
1     1                       What causes muscle spasm?             C   
2     1                       What causes muscle spasm?             C   
3     1                       What causes muscle spasm?             C   
4     1                       What causes muscle spasm?             C   
..   ..                                             ...           ...   
914  75  What is a gene affected by sickle cell anemia?             B   
915  75  What is a gene affected by sickle cell anemia?             B   
916  75  What is a gene affected by sickle cell anemia?             B   
917  75  What is a gene affected by sickle cell anemia?             B   
918  75  What is a gene affected by sickle cell anemia?             B   

         pmid                                              Title  \
0    15902691                                      Muscle cramps   
1    25432724                Diagnosis and treatment of dystonia   
2    29763070                                      Muscle Cramps   
3    29857264  Muscle cramps: A comparison of the two-leading...   
4    30168894              Muscular cramp: causes and management   
..        ...                                                ...   
914  31322815  Combined and differential effects of alpha-tha...   
915  32447424  Functional polymorphisms of BCL11A and HBS1L-M...   
916  32772141  Association between BCL11A, HSB1L-MYB, and Xmn...   
917  33072979  Sickle Cell Disease-Genetics, Pathophysiology,...   
918  33216016  HbF-promoting polymorphisms may specifically r...   

     adaptation_id  abstract_len  \
0                2             7   
1                2             6   
2                2             7   
3                2            11   
4                2             6   
..             ...           ...   
914              3            10   
915              3            13   
916              3            11   
917              3             8   
918              3             5   

                                       input_paragraph  \
0    Muscle cramps are a common problem characteriz...   
1    The dystonias are a group of disorders charact...   
2    Muscle cramps result in continuous, involuntar...   
3    Exercise-Associated Muscle Cramps (EAMC) are a...   
4    Muscular cramp is a common symptom in healthy ...   
..                                                 ...   
914  Background: Our objective was to investigate t...   
915  Fetal hemoglobin (HbF) ameliorates clinical se...   
916  Sickle cell disease (SCD) is a monogenic disea...   
917  Sickle cell disease (SCD) is a monogenetic dis...   
918  Sickle cell anemia (SCA) is a disease characte...   

                                      output_paragraph  
0    Muscle cramps are a common problem represented...  
1    Dystonias are disorders with a lot of uncontro...  
2    Muscle cramps cause constant and unintended co...  
3    Exercise-Associated Muscle Cramps (EAMC) are a...  
4    Muscle cramps are common in healthy people, es...  
..                                                 ...  
914  Researchers analyzed the effects of an alpha-t...  
915  Fetal hemoglobin (HbF) makes the severity of S...  
916  Sickle Cell Disease (SCD) is a genetic blood d...  
917  Sickle Cell Disease (SCD) is a genetic disorde...  
918  Sickle Cell Anemia (SCA) is a genetic blood di...  

[919 rows x 9 columns]

# Comparing & Mapping & Joining - csv vs json

In [196]:
data[~data['pmid'].isin(df_jpara['pmid'])]
# All pmid in csv are in json

Empty DataFrame
Columns: [question, pmid, input_text, target_text, Adaptation_Version, Question_Type]
Index: []

In [197]:
df_jpara[~df_jpara['pmid'].isin(data['pmid'])]

Empty DataFrame
Columns: [QID, Question, Question_Type, pmid, Title, adaptation_id, abstract_len, input_paragraph, output_paragraph]
Index: []

### Mapping & Joining - csv & json

In [198]:
data[data['pmid'] == '33347023']

# dup pmid - 2 adaptations
# no uid
# !!!version_id unable to map

question      pmid                                         input_text  \
791         2  33347023  Purpose: Several studies have previously repor...   
792         2  33347023  Purpose: Several studies have previously repor...   

                                           target_text  Adaptation_Version  \
791  Dry eye, depression, and treatent of depressio...                   2   
792  Studies show that there is a link between depr...                   2   

    Question_Type  
791             B  
792             B

In [199]:
# csv dup adaptation version

dup_list = [
    #train
    '33160639','32775988','26093176','27600582',

    #test
    '21462113','30377698','24259556','3630857','20200254',
    '12090459','21636864','16372518','24619814','17916952',
    '32631287','19306923','28665969',

    #val
    '33347023', '30249798','34397423','15316838','30838456'
]

In [200]:
dj['2']['33347023']['adaptations']

{'adaptation3': {'1': 'Studies show that there is a link between depression treatment and dry eyes.',
  '2': 'This study looks at the tears of depressed people when given different types of drugs that treat depression.',
  '3': 'This study includes 132 people taking antidepressant drugs and 58 people not taking antidepressant drugs for comparison.',
  '4': 'Patients were taking the antidepressant drugs called venlafaxine, duloxetine, escitalopram, and sertraline.',
  '5': 'Patients filled our a form to measure their level of depression.',
  '6': 'The researchers looked at the eyes and tears of the patients.',
  '7': 'Patients filled out a form to measure the dryness of their eyes.',
  '8': '',
  '9': 'Those people taking antidepressant drugs had drier eyes than those that were not taking antidepressant drugs.',
  '10': 'The people taking duloxetine had the driest eyes.',
  '11': 'The people taking antidepressant drugs scored much higher on a test to measure dry eyes.',
  '12': 'This st

### Json - df_jsent vs df_jpara

In [201]:
df_jpara[df_jpara['pmid'] == '33160639']

QID                               Question Question_Type      pmid  \
37   3  How can i reduce my potassium levels?             C  33160639   
38   3  How can i reduce my potassium levels?             C  33160639   

                                  Title  adaptation_id  abstract_len  \
37  Clinical Management of Hyperkalemia              3            10   
38  Clinical Management of Hyperkalemia              2            10   

                                      input_paragraph  \
37  Hyperkalemia is an electrolyte abnormality wit...   
38  Hyperkalemia is an electrolyte abnormality wit...   

                                     output_paragraph  
37  Hyperkalemia is a condition where the potassiu...  
38  Hyperkalemia (high blood potassium) is an elec...

In [202]:
df_jsent[df_jsent['pmid'] == '33160639']

QID                               Question Question_Type      pmid  \
342   3  How can i reduce my potassium levels?             C  33160639   
343   3  How can i reduce my potassium levels?             C  33160639   
344   3  How can i reduce my potassium levels?             C  33160639   
345   3  How can i reduce my potassium levels?             C  33160639   
346   3  How can i reduce my potassium levels?             C  33160639   
347   3  How can i reduce my potassium levels?             C  33160639   
348   3  How can i reduce my potassium levels?             C  33160639   
349   3  How can i reduce my potassium levels?             C  33160639   
350   3  How can i reduce my potassium levels?             C  33160639   
351   3  How can i reduce my potassium levels?             C  33160639   
352   3  How can i reduce my potassium levels?             C  33160639   
353   3  How can i reduce my potassium levels?             C  33160639   
354   3  How can i reduce my potassium levels?             C  33160639   
355   3  How can i reduce my potassium levels?             C  33160639   
356   3  How can i reduce my potassium levels?             C  33160639   
357   3  How can i reduce my potassium levels?             C  33160639   
358   3  How can i reduce my potassium levels?             C  33160639   
359   3  How can i reduce my potassium levels?             C  33160639   
360   3  How can i reduce my potassium levels?             C  33160639   
361   3  How can i reduce my potassium levels?             C  33160639   

                                   Title  adaptation_id  abstract_len  \
342  Clinical Management of Hyperkalemia              3            10   
343  Clinical Management of Hyperkalemia              3            10   
344  Clinical Management of Hyperkalemia              3            10   
345  Clinical Management of Hyperkalemia              3            10   
346  Clinical Management of Hyperkalemia              3            10   
347  Clinical Management of Hyperkalemia              3            10   
348  Clinical Management of Hyperkalemia              3            10   
349  Clinical Management of Hyperkalemia              3            10   
350  Clinical Management of Hyperkalemia              3            10   
351  Clinical Management of Hyperkalemia              3            10   
352  Clinical Management of Hyperkalemia              2            10   
353  Clinical Management of Hyperkalemia              2            10   
354  Clinical Management of Hyperkalemia              2            10   
355  Clinical Management of Hyperkalemia              2            10   
356  Clinical Management of Hyperkalemia              2            10   
357  Clinical Management of Hyperkalemia              2            10   
358  Clinical Management of Hyperkalemia              2            10   
359  Clinical Management of Hyperkalemia              2            10   
360  Clinical Management of Hyperkalemia              2            10   
361  Clinical Management of Hyperkalemia              2            10   

    Abstract_sentence_id                                           Abstract  \
342                    1  Hyperkalemia is an electrolyte abnormality wit...   
343                    2  Despite various guidelines, no universally acc...   
344                    3  Based on the available evidence, this review i...   
345                    4  Real-world studies are needed for a better und...   
346                    5  There is a need to improve effective managemen...   
347                    6  Monitoring serum K+ should be individualized; ...   
348                    7  Recent clinical studies suggest that the newer...   
349                    8  Enhancing the knowledge of primary care physic...   
350                    9  Lastly, the availability of newer K+-binding a...   
351                   10  Individualized monitoring of serum K+ among pa...   
352                    1  Hyperkalemia is an e

In [203]:
df_jpara['QID'] = df_jpara['QID'].astype(int)
df_jsent['QID'] = df_jsent['QID'].astype(int)

In [204]:
df_jmerged = df_jsent.merge(df_jpara, on=['QID', 'pmid', 'adaptation_id'], how='left')

In [205]:
df_jmerged

QID                                      Question_x Question_Type_x  \
0       1                       What causes muscle spasm?               C   
1       1                       What causes muscle spasm?               C   
2       1                       What causes muscle spasm?               C   
3       1                       What causes muscle spasm?               C   
4       1                       What causes muscle spasm?               C   
...   ...                                             ...             ...   
9313   75  What is a gene affected by sickle cell anemia?               B   
9314   75  What is a gene affected by sickle cell anemia?               B   
9315   75  What is a gene affected by sickle cell anemia?               B   
9316   75  What is a gene affected by sickle cell anemia?               B   
9317   75  What is a gene affected by sickle cell anemia?               B   

          pmid                                            Title_x  \
0     15902691                                      Muscle cramps   
1     15902691                                      Muscle cramps   
2     15902691                                      Muscle cramps   
3     15902691                                      Muscle cramps   
4     15902691                                      Muscle cramps   
...        ...                                                ...   
9313  33216016  HbF-promoting polymorphisms may specifically r...   
9314  33216016  HbF-promoting polymorphisms may specifically r...   
9315  33216016  HbF-promoting polymorphisms may specifically r...   
9316  33216016  HbF-promoting polymorphisms may specifically r...   
9317  33216016  HbF-promoting polymorphisms may specifically r...   

      adaptation_id  abstract_len_x Abstract_sentence_id  \
0                 2               7                    1   
1                 2               7                    2   
2                 2               7                    3   
3                 2               7                    4   
4                 2               7                    5   
...             ...             ...                  ...   
9313              3               5                    1   
9314              3               5                    2   
9315              3               5                    3   
9316              3               5                    4   
9317              3               5                    5   

                                               Abstract  \
0     Muscle cramps are a common problem characteriz...   
1     These true cramps, which originate from periph...   
2     Medical history, physical examination, and a l...   
3     Despite the "benign" nature of cramps, many pa...   
4     Treatment options are guided both by experienc...   
...                                                 ...   
9313  Sickle cell anemia (SCA) is a disease characte...   
9314  Because of their effects on HbS polymerization...   
9315  The aim of our study was to determine if the n...   
9316  Our results confirmed that alpha-thalassemia p...   
9317  We also showed that more HbF-QTL may provide a...   

     Adaptation_sentence_id  \
0                         1   
1                         2   
2                         3   
3                         4   
4                         5   
...                     ...   
9313                      1   
9314                      2   
9315                      3   
9316                      4   
9317                      5   

                                             Adaptation  \
0     Muscle cramps are a common problem represented...   
1     These true cramps, coming from nerves outside ...   
2     Medical history, physical check-up, and lab sc...   
3     Despite their harmless nature, cramps are unco...   
4     Experience and limited medical studies guide t...   
...                                                 ...   
9313  Sickle Cell Anemia (SCA) is a 

# Paragraph Segmentation

In [206]:
df_jpara['input_paragraph']

0      Muscle cramps are a common problem characteriz...
1      The dystonias are a group of disorders charact...
2      Muscle cramps result in continuous, involuntar...
3      Exercise-Associated Muscle Cramps (EAMC) are a...
4      Muscular cramp is a common symptom in healthy ...
                             ...                        
914    Background: Our objective was to investigate t...
915    Fetal hemoglobin (HbF) ameliorates clinical se...
916    Sickle cell disease (SCD) is a monogenic disea...
917    Sickle cell disease (SCD) is a monogenetic dis...
918    Sickle cell anemia (SCA) is a disease characte...
Name: input_paragraph, Length: 919, dtype: object

In [ ]:
# 'input_paragraph' full text , 'Abstract' sentences

### Rule based

In [ ]:
# # Split text based on custom delimiter
# sentences = text.split("|||")
# # !!! No | \t \n ". "

# t0 = df_jpara['input_paragraph'][0]
# s0 = t0.split(". ")
# for i, s in enumerate(s0, 1):
#     print(f"S {i}: {s}")

In [ ]:
# import re

# t0 = df_jpara['input_paragraph'][0]
# # Split text into sentences based on punctuation
# s0 = re.split(r'[.!?]', t0)

# for i, s in enumerate(s0, 1):
#   print(f"S {i}: {s}")

S 1: Muscle cramps are a common problem characterized by a sudden, painful, involuntary contraction of muscle
S 2: These true cramps, which originate from peripheral nerves, may be distinguished from other muscle pain or spasm
S 3: Medical history, physical examination, and a limited laboratory screen help to determine the various causes of muscle cramps
S 4: Despite the "benign" nature of cramps, many patients find the symptom very uncomfortable
S 5: Treatment options are guided both by experience and by a limited number of therapeutic trials
S 6: Quinine sulfate is an effective medication, but the side-effect profile is worrisome, and other membrane-stabilizing drugs are probably just as effective
S 7: Patients will benefit from further studies to better define the pathophysiology of muscle cramps and to find more effective medications with fewer side-effects
S 8: 


In [207]:
df_jpara[df_jpara['pmid']=='34408570']
# example with decimal points

QID                                           Question Question_Type  \
590   45  Do i keep a pressure sore covered and moist an...             C   
591   45  Do i keep a pressure sore covered and moist an...             C   

         pmid                                              Title  \
590  34408570  Evaluation of the therapeutic efficacy of acti...   
591  34408570  Evaluation of the therapeutic efficacy of acti...   

     adaptation_id  abstract_len  \
590              1            10   
591              2            10   

                                       input_paragraph  \
590  Introduction: Treatment of decubitus ulcers is...   
591  Introduction: Treatment of decubitus ulcers is...   

                                      output_paragraph  
590  Treatment of bedsores is a serious medical pro...  
591  Treating decubitus ulcers (bedsores) is a seri...

In [208]:
def t2s(text):
    sentence_pattern = r'(?<=[.!?])(?=[^0-9])'
    sentences = re.split(sentence_pattern, text)

    return sentences

t0 = df_jpara['input_paragraph'][590]
s0 = t2s(t0)

for i, s in enumerate(s0, 0):
  print(f"S {i}: {s}")


S 0: Introduction: Treatment of decubitus ulcers is a grave medical problem.
S 1: In many cases, it is difficult to cure a pressure ulcer, especially when it is deep and extensive, and prognosis is usually unfavourable.
S 2: Treatment of decubitus ulcers requires new specialist dressings, which play an important role in the healing process.
S 3: Aim: To evaluate therapeutic efficacy of active specialist medical dressings in the treatment of decubitus.
S 4: Material and methods: Research involved 40 patients - 18 (45%) women and 22 (55%) men, suffering from decubitus ulcers of different size and depth, localized in the sacral region, lasting from 1.5 to 30 months.
S 5: Patients were randomly assigned to two research groups (20 people each), were treated for 4 weeks with 2 different specialist dressings.
S 6: ATRAUMAN Ag, which contains silver ions, was used in the first group, while paraffin gauze of BACTIGRAS type was used in the second group.
S 7: An assessment of pressure ulcers' hea

In [209]:
rs_list = []

for index, row in df_jpara.iterrows():
  abstract = row['input_paragraph']
  sent_abstract = t2s(abstract)

  for i, sentence in enumerate(sent_abstract, 1):
    row = {
        'QID': df_jpara.at[index, 'QID'],
        'Question': df_jpara.at[index, 'Question'],
        'Question_Type': df_jpara.at[index, 'Question_Type'],
        'pmid': df_jpara.at[index, 'pmid'],
        'Title': df_jpara.at[index, 'Title'],
        'adaptation_id': df_jpara.at[index, 'adaptation_id'],
        'abstract_len': df_jpara.at[index, 'abstract_len'],
        'segmented__sentence_id': i,
        'segmented_sentence': sentence
    }
    rs_list.append(row)

df_s_r = pd.DataFrame(rs_list)

In [210]:
df_s_r

QID                                        Question Question_Type  \
0       1                       What causes muscle spasm?             C   
1       1                       What causes muscle spasm?             C   
2       1                       What causes muscle spasm?             C   
3       1                       What causes muscle spasm?             C   
4       1                       What causes muscle spasm?             C   
...   ...                                             ...           ...   
9662   75  What is a gene affected by sickle cell anemia?             B   
9663   75  What is a gene affected by sickle cell anemia?             B   
9664   75  What is a gene affected by sickle cell anemia?             B   
9665   75  What is a gene affected by sickle cell anemia?             B   
9666   75  What is a gene affected by sickle cell anemia?             B   

          pmid                                              Title  \
0     15902691                                      Muscle cramps   
1     15902691                                      Muscle cramps   
2     15902691                                      Muscle cramps   
3     15902691                                      Muscle cramps   
4     15902691                                      Muscle cramps   
...        ...                                                ...   
9662  33216016  HbF-promoting polymorphisms may specifically r...   
9663  33216016  HbF-promoting polymorphisms may specifically r...   
9664  33216016  HbF-promoting polymorphisms may specifically r...   
9665  33216016  HbF-promoting polymorphisms may specifically r...   
9666  33216016  HbF-promoting polymorphisms may specifically r...   

      adaptation_id  abstract_len  segmented__sentence_id  \
0                 2             7                       1   
1                 2             7                       2   
2                 2             7                       3   
3                 2             7                       4   
4                 2             7                       5   
...             ...           ...                     ...   
9662              3             5                       1   
9663              3             5                       2   
9664              3             5                       3   
9665              3             5                       4   
9666              3             5                       5   

                                     segmented_sentence  
0     Muscle cramps are a common problem characteriz...  
1     These true cramps, which originate from periph...  
2     Medical history, physical examination, and a l...  
3     Despite the "benign" nature of cramps, many pa...  
4     Treatment options are guided both by experienc...  
...                                                 ...  
9662  Sickle cell anemia (SCA) is a disease characte...  
9663  Because of their effects on HbS polymerization...  
9664  The aim of our study was to determine if the n...  
9665  Our results confirmed that alpha-thalassemia p...  
9666  We also showed that more HbF-QTL may provide a...  

[9667 rows x 9 columns]

### Pre-trained language model - Spacy

In [211]:
t0 = df_jpara['input_paragraph'][0]
s0 = sent_tokenize(t0)

for i, s in enumerate(s0, 1):
  print(f"S {i}: {s}")

# nltk does not work

S 1: Muscle cramps are a common problem characterized by a sudden, painful, involuntary contraction of muscle.These true cramps, which originate from peripheral nerves, may be distinguished from other muscle pain or spasm.Medical history, physical examination, and a limited laboratory screen help to determine the various causes of muscle cramps.Despite the "benign" nature of cramps, many patients find the symptom very uncomfortable.Treatment options are guided both by experience and by a limited number of therapeutic trials.Quinine sulfate is an effective medication, but the side-effect profile is worrisome, and other membrane-stabilizing drugs are probably just as effective.Patients will benefit from further studies to better define the pathophysiology of muscle cramps and to find more effective medications with fewer side-effects.


In [ ]:
# nlp = spacy.load('en_core_web_sm')

# test = data['input_text'][0]

# doc = nlp(test)

# sentences = [sent.text for sent in doc.sents]

# for i, sentence in enumerate(sentences, 1):
#     print(f'Sentence {i}: {sentence}')


Sentence 1: Exercise-Associated Muscle Cramps (EAMC) are a common painful condition of muscle spasms.
Sentence 2: Despite scientists tried to understand the physiological mechanism that underlies these common phenomena, the etiology is still unclear.
Sentence 3: From 1900 to nowadays, the scientific world retracted several times the original hypothesis of heat cramps.
Sentence 4: However, recent literature seems to focus on two potential mechanisms: the dehydration or electrolyte depletion mechanism, and the neuromuscular mechanism.
Sentence 5: The aim of this review is to examine the recent literature, in terms of physiological mechanisms of EAMC.
Sentence 6: A comprehensive search was conducted on PubMed and Google Scholar.
Sentence 7: The following terminology was applied: muscle cramps, neuromuscular hypothesis (or thesis), dehydration hypothesis, Exercise-Associated muscle cramps, nocturnal cramps, muscle spasm, muscle fatigue.
Sentence 8: From the initial literature of 424 manusc

In [ ]:
# sentences = pd.DataFrame(columns=['pmid','csv_input_text', 'csv_target_text', 'abstract_sentences', 'adaptation_sentences'])

In [ ]:
# for index, row in data.iterrows():
#   abstract = row['input_text']
#   doc_abstract = nlp(abstract)

#   adaptation = row['target_text']
#   doc_adaptation = nlp(adaptation)

#   sent_abstract = [sent.text for sent in doc_abstract.sents]
#   sent_adaptation = [sent.text for sent in doc_adaptation.sents]

#   for i, o in zip(sent_abstract, sent_adaptation):
#     new_row = {'pmid': row['pmid'], 'csv_input_text': row['input_text'], 'csv_target_text': row['target_text'],
#                'abstract_sentences': i, 'adaptation_sentences': o }
#     sentences = sentences.append(new_row, ignore_index=True)

Streaming output truncated to the last 5000 lines.
<ipython-input-17-a0f1e7549cc3>:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sentences = sentences.append(new_row, ignore_index=True)
<ipython-input-17-a0f1e7549cc3>:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sentences = sentences.append(new_row, ignore_index=True)
<ipython-input-17-a0f1e7549cc3>:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sentences = sentences.append(new_row, ignore_index=True)
<ipython-input-17-a0f1e7549cc3>:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  sentences = sentences.append(new_row, ignore_index=True)
<ipython-input-17-a0f1e7549cc3>:19: F

In [ ]:
# sentences.to_csv('segmented_sentences_spacy_v2.csv', index=False)
# for Xiaohui's test model - 22.10.17  (not accurate, better use json instead)

In [212]:
nlp = spacy.load('en_core_web_sm')

In [213]:
df_jpara.head(5)

QID                   Question Question_Type      pmid  \
0    1  What causes muscle spasm?             C  15902691   
1    1  What causes muscle spasm?             C  25432724   
2    1  What causes muscle spasm?             C  29763070   
3    1  What causes muscle spasm?             C  29857264   
4    1  What causes muscle spasm?             C  30168894   

                                               Title  adaptation_id  \
0                                      Muscle cramps              2   
1                Diagnosis and treatment of dystonia              2   
2                                      Muscle Cramps              2   
3  Muscle cramps: A comparison of the two-leading...              2   
4              Muscular cramp: causes and management              2   

   abstract_len                                    input_paragraph  \
0             7  Muscle cramps are a common problem characteriz...   
1             6  The dystonias are a group of disorders charact...   
2             7  Muscle cramps result in continuous, involuntar...   
3            11  Exercise-Associated Muscle Cramps (EAMC) are a...   
4             6  Muscular cramp is a common symptom in healthy ...   

                                    output_paragraph  
0  Muscle cramps are a common problem represented...  
1  Dystonias are disorders with a lot of uncontro...  
2  Muscle cramps cause constant and unintended co...  
3  Exercise-Associated Muscle Cramps (EAMC) are a...  
4  Muscle cramps are common in healthy people, es...

In [214]:
s_list = []

for index, row in df_jpara.iterrows():
  abstract = row['input_paragraph']
  doc_abstract = nlp(abstract)

  sent_abstract = [sent.text for sent in doc_abstract.sents]

  for i, sentence in enumerate(sent_abstract, 1):
    row = {
        'QID': df_jpara.at[index, 'QID'],
        'Question': df_jpara.at[index, 'Question'],
        'Question_Type': df_jpara.at[index, 'Question_Type'],
        'pmid': df_jpara.at[index, 'pmid'],
        'Title': df_jpara.at[index, 'Title'],
        'adaptation_id': df_jpara.at[index, 'adaptation_id'],
        'abstract_len': df_jpara.at[index, 'abstract_len'],
        'segmented__sentence_id': i,
        'segmented_sentence': sentence
    }
    s_list.append(row)

df_s_lm = pd.DataFrame(s_list)

In [215]:
df_s_lm

QID                                        Question Question_Type  \
0       1                       What causes muscle spasm?             C   
1       1                       What causes muscle spasm?             C   
2       1                       What causes muscle spasm?             C   
3       1                       What causes muscle spasm?             C   
4       1                       What causes muscle spasm?             C   
...   ...                                             ...           ...   
8267   75  What is a gene affected by sickle cell anemia?             B   
8268   75  What is a gene affected by sickle cell anemia?             B   
8269   75  What is a gene affected by sickle cell anemia?             B   
8270   75  What is a gene affected by sickle cell anemia?             B   
8271   75  What is a gene affected by sickle cell anemia?             B   

          pmid                                              Title  \
0     15902691                                      Muscle cramps   
1     15902691                                      Muscle cramps   
2     15902691                                      Muscle cramps   
3     15902691                                      Muscle cramps   
4     15902691                                      Muscle cramps   
...        ...                                                ...   
8267  33216016  HbF-promoting polymorphisms may specifically r...   
8268  33216016  HbF-promoting polymorphisms may specifically r...   
8269  33216016  HbF-promoting polymorphisms may specifically r...   
8270  33216016  HbF-promoting polymorphisms may specifically r...   
8271  33216016  HbF-promoting polymorphisms may specifically r...   

      adaptation_id  abstract_len  segmented__sentence_id  \
0                 2             7                       1   
1                 2             7                       2   
2                 2             7                       3   
3                 2             7                       4   
4                 2             7                       5   
...             ...           ...                     ...   
8267              3             5                       1   
8268              3             5                       2   
8269              3             5                       3   
8270              3             5                       4   
8271              3             5                       5   

                                     segmented_sentence  
0     Muscle cramps are a common problem characteriz...  
1     These true cramps, which originate from periph...  
2     Medical history, physical examination, and a l...  
3     Despite the "benign" nature of cramps, many pa...  
4     Treatment options are guided both by experienc...  
...                                                 ...  
8267  Sickle cell anemia (SCA) is a disease characte...  
8268  Because of their effects on HbS polymerization...  
8269  The aim of our study was to determine if the n...  
8270  Our results confirmed that alpha-thalassemia p...  
8271  We also showed that more HbF-QTL may provide a...  

[8272 rows x 9 columns]

# Model evaluation

In [ ]:
# 1. score for sentences

# 2. text similarity - break by space (match of words) average



### 1. Score
- sentences for each text


In [216]:
df_jmerged['sent_len'] = df_jmerged['Abstract'].apply(lambda x: len(x))

In [217]:
df_jmerged

QID                                      Question_x Question_Type_x  \
0       1                       What causes muscle spasm?               C   
1       1                       What causes muscle spasm?               C   
2       1                       What causes muscle spasm?               C   
3       1                       What causes muscle spasm?               C   
4       1                       What causes muscle spasm?               C   
...   ...                                             ...             ...   
9313   75  What is a gene affected by sickle cell anemia?               B   
9314   75  What is a gene affected by sickle cell anemia?               B   
9315   75  What is a gene affected by sickle cell anemia?               B   
9316   75  What is a gene affected by sickle cell anemia?               B   
9317   75  What is a gene affected by sickle cell anemia?               B   

          pmid                                            Title_x  \
0     15902691                                      Muscle cramps   
1     15902691                                      Muscle cramps   
2     15902691                                      Muscle cramps   
3     15902691                                      Muscle cramps   
4     15902691                                      Muscle cramps   
...        ...                                                ...   
9313  33216016  HbF-promoting polymorphisms may specifically r...   
9314  33216016  HbF-promoting polymorphisms may specifically r...   
9315  33216016  HbF-promoting polymorphisms may specifically r...   
9316  33216016  HbF-promoting polymorphisms may specifically r...   
9317  33216016  HbF-promoting polymorphisms may specifically r...   

      adaptation_id  abstract_len_x Abstract_sentence_id  \
0                 2               7                    1   
1                 2               7                    2   
2                 2               7                    3   
3                 2               7                    4   
4                 2               7                    5   
...             ...             ...                  ...   
9313              3               5                    1   
9314              3               5                    2   
9315              3               5                    3   
9316              3               5                    4   
9317              3               5                    5   

                                               Abstract  \
0     Muscle cramps are a common problem characteriz...   
1     These true cramps, which originate from periph...   
2     Medical history, physical examination, and a l...   
3     Despite the "benign" nature of cramps, many pa...   
4     Treatment options are guided both by experienc...   
...                                                 ...   
9313  Sickle cell anemia (SCA) is a disease characte...   
9314  Because of their effects on HbS polymerization...   
9315  The aim of our study was to determine if the n...   
9316  Our results confirmed that alpha-thalassemia p...   
9317  We also showed that more HbF-QTL may provide a...   

     Adaptation_sentence_id  \
0                         1   
1                         2   
2                         3   
3                         4   
4                         5   
...                     ...   
9313                      1   
9314                      2   
9315                      3   
9316                      4   
9317                      5   

                                             Adaptation  \
0     Muscle cramps are a common problem represented...   
1     These true cramps, coming from nerves outside ...   
2     Medical history, physical check-up, and lab sc...   
3     Despite their harmless nature, cramps are unco...   
4     Experience and limited medical studies guide t...   
...                                                 ...   
9313  Sickle Cell Anemia (SCA) is a 

In [218]:
df_jmerged['sent_len_t2s'] = df_jmerged['Abstract'].apply(lambda x: len(t2s(x)))

In [219]:
def spacy2s(text):
  doc_abstract = nlp(text)
  sentences = [sent.text for sent in doc_abstract.sents]

  return sentences

t0 = df_jpara['input_paragraph'][590]
s0 = spacy2s(t0)

for i, s in enumerate(s0, 1):
  print(f"S {i}: {s}")

S 1: Introduction: Treatment of decubitus ulcers is a grave medical problem.
S 2: In many cases, it is difficult to cure a pressure ulcer, especially when it is deep and extensive, and prognosis is usually unfavourable.
S 3: Treatment of decubitus ulcers requires new specialist dressings, which play an important role in the healing process.
S 4: Aim: To evaluate therapeutic efficacy of active specialist medical dressings in the treatment of decubitus.
S 5: Material and methods: Research involved 40 patients - 18 (45%) women and 22 (55%) men, suffering from decubitus ulcers of different size and depth, localized in the sacral region, lasting from 1.5 to 30 months.
S 6: Patients were randomly assigned to two research groups (20 people each), were treated for 4 weeks with 2 different specialist dressings.
S 7: ATRAUMAN Ag, which contains silver ions, was used in the first group, while paraffin gauze of BACTIGRAS type was used in the second group.
S 8: An assessment of pressure ulcers' hea

In [220]:
df_jmerged['sent_len_t2s'] = df_jmerged['input_paragraph'].apply(lambda x: len(t2s(x)))

In [221]:
df_jmerged['sent_len_spacy2s'] = df_jmerged['input_paragraph'].apply(lambda x: len(spacy2s(x)))

In [222]:
df_jmerged_p = df_jmerged.pivot_table(index = ['QID', 'pmid', 'adaptation_id'],
                                      values=['abstract_len_x', 'sent_len_t2s', 'sent_len_spacy2s'],
                                      aggfunc={'abstract_len_x': 'count', 'sent_len_t2s': 'mean', 'sent_len_spacy2s': 'mean'})
df_jmerged_p

abstract_len_x  sent_len_spacy2s  sent_len_t2s
QID pmid     adaptation_id                                                
1   15902691 2                           7                 7             7
    25432724 2                           6                 6             6
    29763070 2                           7                 7             7
    29857264 2                          11                10            11
    30168894 2                           6                 6             6
...                                    ...               ...           ...
75  31322815 3                          10                 6            10
    32447424 3                          13                 6            13
    32772141 3                          11                11            11
    33072979 3                           8                 8             8
    33216016 3                           5                 5             5

[919 rows x 3 columns]

In [223]:
correct_predictions = (df_jmerged_p['abstract_len_x'] == df_jmerged_p['sent_len_t2s']).sum()
accuracy_r = correct_predictions / len(df_jmerged_p)
print("Accuracy:", accuracy_r)

Accuracy: 0.8443960826985855


In [224]:
correct_predictions = (df_jmerged_p['abstract_len_x'] == df_jmerged_p['sent_len_spacy2s']).sum()
accuracy_s = correct_predictions / len(df_jmerged_p)
print("Accuracy:", accuracy_s)

Accuracy: 0.36887921653971706


In [225]:
mse_r = mean_squared_error(df_jmerged_p['abstract_len_x'], df_jmerged_p['sent_len_t2s'])

print("Mean Squared Error:", mse_r)

Mean Squared Error: 2.571273122959739


In [226]:
mse_s = mean_squared_error(df_jmerged_p['abstract_len_x'], df_jmerged_p['sent_len_spacy2s'])

print("Mean Squared Error:", mse_s)

Mean Squared Error: 4.404787812840044


### 2. Text similarity
  - break by space (match of words) average

In [227]:
df_actual = df_jmerged[['QID','pmid','adaptation_id','abstract_len_x','Adaptation_sentence_id','Abstract']]

In [228]:
df_actual

QID      pmid  adaptation_id  abstract_len_x Adaptation_sentence_id  \
0       1  15902691              2               7                      1   
1       1  15902691              2               7                      2   
2       1  15902691              2               7                      3   
3       1  15902691              2               7                      4   
4       1  15902691              2               7                      5   
...   ...       ...            ...             ...                    ...   
9313   75  33216016              3               5                      1   
9314   75  33216016              3               5                      2   
9315   75  33216016              3               5                      3   
9316   75  33216016              3               5                      4   
9317   75  33216016              3               5                      5   

                                               Abstract  
0     Muscle cramps are a common problem characteriz...  
1     These true cramps, which originate from periph...  
2     Medical history, physical examination, and a l...  
3     Despite the "benign" nature of cramps, many pa...  
4     Treatment options are guided both by experienc...  
...                                                 ...  
9313  Sickle cell anemia (SCA) is a disease characte...  
9314  Because of their effects on HbS polymerization...  
9315  The aim of our study was to determine if the n...  
9316  Our results confirmed that alpha-thalassemia p...  
9317  We also showed that more HbF-QTL may provide a...  

[9318 rows x 6 columns]

In [229]:
df_actual.rename(columns={'abstract_len_x': 'abstract_len','Adaptation_sentence_id': 'segmented__sentence_id'}, inplace=True)

<ipython-input-229-cf391de32da8>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_actual.rename(columns={'abstract_len_x': 'abstract_len','Adaptation_sentence_id': 'segmented__sentence_id'}, inplace=True)


In [230]:
df_rule = df_s_r[['QID','pmid','adaptation_id','abstract_len','segmented__sentence_id','segmented_sentence']]
# rule based

In [231]:
df_rule

QID      pmid  adaptation_id  abstract_len  segmented__sentence_id  \
0       1  15902691              2             7                       1   
1       1  15902691              2             7                       2   
2       1  15902691              2             7                       3   
3       1  15902691              2             7                       4   
4       1  15902691              2             7                       5   
...   ...       ...            ...           ...                     ...   
9662   75  33216016              3             5                       1   
9663   75  33216016              3             5                       2   
9664   75  33216016              3             5                       3   
9665   75  33216016              3             5                       4   
9666   75  33216016              3             5                       5   

                                     segmented_sentence  
0     Muscle cramps are a common problem characteriz...  
1     These true cramps, which originate from periph...  
2     Medical history, physical examination, and a l...  
3     Despite the "benign" nature of cramps, many pa...  
4     Treatment options are guided both by experienc...  
...                                                 ...  
9662  Sickle cell anemia (SCA) is a disease characte...  
9663  Because of their effects on HbS polymerization...  
9664  The aim of our study was to determine if the n...  
9665  Our results confirmed that alpha-thalassemia p...  
9666  We also showed that more HbF-QTL may provide a...  

[9667 rows x 6 columns]

In [232]:
df_spacy = df_s_lm[['QID','pmid','adaptation_id','abstract_len','segmented__sentence_id','segmented_sentence']]
# spacy

In [234]:
df_actual['segmented__sentence_id'] = df_actual['segmented__sentence_id'].astype(int)

<ipython-input-234-2994e8378b89>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_actual['segmented__sentence_id'] = df_actual['segmented__sentence_id'].astype(int)


In [235]:
df_sent_comparison = df_actual.merge(df_rule, on=['QID', 'pmid', 'adaptation_id','segmented__sentence_id'], how='left')

In [236]:
df_sent_comparison.rename(columns={'segmented_sentence': 'segmented_sentence_rule'}, inplace=True)

In [237]:
df_sent_comparison = df_sent_comparison.merge(df_spacy, on=['QID', 'pmid', 'adaptation_id','segmented__sentence_id'], how='left')

In [238]:
df_sent_comparison.rename(columns={'segmented_sentence': 'segmented_sentence_spacy'}, inplace=True)

In [239]:
df_sent_comparison

QID      pmid  adaptation_id  abstract_len_x  segmented__sentence_id  \
0       1  15902691              2               7                       1   
1       1  15902691              2               7                       2   
2       1  15902691              2               7                       3   
3       1  15902691              2               7                       4   
4       1  15902691              2               7                       5   
...   ...       ...            ...             ...                     ...   
9313   75  33216016              3               5                       1   
9314   75  33216016              3               5                       2   
9315   75  33216016              3               5                       3   
9316   75  33216016              3               5                       4   
9317   75  33216016              3               5                       5   

                                               Abstract  abstract_len_y  \
0     Muscle cramps are a common problem characteriz...             7.0   
1     These true cramps, which originate from periph...             7.0   
2     Medical history, physical examination, and a l...             7.0   
3     Despite the "benign" nature of cramps, many pa...             7.0   
4     Treatment options are guided both by experienc...             7.0   
...                                                 ...             ...   
9313  Sickle cell anemia (SCA) is a disease characte...             5.0   
9314  Because of their effects on HbS polymerization...             5.0   
9315  The aim of our study was to determine if the n...             5.0   
9316  Our results confirmed that alpha-thalassemia p...             5.0   
9317  We also showed that more HbF-QTL may provide a...             5.0   

                                segmented_sentence_rule  abstract_len  \
0     Muscle cramps are a common problem characteriz...           7.0   
1     These true cramps, which originate from periph...           7.0   
2     Medical history, physical examination, and a l...           7.0   
3     Despite the "benign" nature of cramps, many pa...           7.0   
4     Treatment options are guided both by experienc...           7.0   
...                                                 ...           ...   
9313  Sickle cell anemia (SCA) is a disease characte...           5.0   
9314  Because of their effects on HbS polymerization...           5.0   
9315  The aim of our study was to determine if the n...           5.0   
9316  Our results confirmed that alpha-thalassemia p...           5.0   
9317  We also showed that more HbF-QTL may provide a...           5.0   

                               segmented_sentence_spacy  
0     Muscle cramps are a common problem characteriz...  
1     These true cramps, which originate from periph...  
2     Medical history, physical examination, and a l...  
3     Despite the "benign" nature of cramps, many pa...  
4     Treatment options are guided both by experienc...  
...                                                 ...  
9313  Sickle cell anemia (SCA) is a disease characte...  
9314  Because of their effects on HbS polymerization...  
9315  The aim of our study was to determine if the n...  
9316  Our results confirmed that alpha-thalassemia p...  
9317  We also showed that more HbF-QTL may provide a...  

[9318 rows x 10 columns]

In [240]:
df_sent_comparison['accuracy_rule'] = df_sent_comparison['Abstract'] == df_sent_comparison['segmented_sentence_rule']

TA = (df_sent_comparison['accuracy_rule'].sum() / len(df_sent_comparison)) * 100

print("Text Accuracy with rule: {:.2f}%".format(TA))

Text Accuracy with rule: 88.81%


In [241]:
df_sent_comparison['accuracy_spacy'] = df_sent_comparison['Abstract'] == df_sent_comparison['segmented_sentence_spacy']

# Calculate accuracy as the percentage of correct predictions
TA = (df_sent_comparison['accuracy_spacy'].sum() / len(df_sent_comparison)) * 100

print("Text Accuracy with spacy: {:.2f}%".format(TA))


Text Accuracy with spacy: 43.97%


In [242]:
df_sent_comparison.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9318 entries, 0 to 9317
Data columns (total 12 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   QID                       9318 non-null   int64  
 1   pmid                      9318 non-null   object 
 2   adaptation_id             9318 non-null   int64  
 3   abstract_len_x            9318 non-null   int64  
 4   segmented__sentence_id    9318 non-null   int64  
 5   Abstract                  9318 non-null   object 
 6   abstract_len_y            9303 non-null   float64
 7   segmented_sentence_rule   9303 non-null   object 
 8   abstract_len              8161 non-null   float64
 9   segmented_sentence_spacy  8161 non-null   object 
 10  accuracy_rule             9318 non-null   bool   
 11  accuracy_spacy            9318 non-null   bool   
dtypes: bool(2), float64(2), int64(4), object(4)
memory usage: 819.0+ KB


In [243]:
df_sent_comparison['Abstract'] = df_sent_comparison['Abstract'].astype(str)
df_sent_comparison['segmented_sentence_rule'] = df_sent_comparison['segmented_sentence_rule'].astype(str)
df_sent_comparison['segmented_sentence_spacy'] = df_sent_comparison['segmented_sentence_spacy'].astype(str)

In [244]:
df_sent_comparison['word_len_act'] = df_sent_comparison['Abstract'].apply(lambda x: len(x))
df_sent_comparison['word_len_rule'] = df_sent_comparison['segmented_sentence_rule'].apply(lambda x: len(x))
df_sent_comparison['word_len_spacy'] = df_sent_comparison['segmented_sentence_spacy'].apply(lambda x: len(x))

In [245]:
mse_rw = mean_squared_error(df_sent_comparison['word_len_act'], df_sent_comparison['word_len_rule'])

print("Mean Squared Error for rule:", mse_rw)

Mean Squared Error for rule: 1556.6333977248337


In [246]:
mse_sw = mean_squared_error(df_sent_comparison['word_len_act'], df_sent_comparison['word_len_spacy'])

print("Mean Squared Error for spacy:", mse_sw)

Mean Squared Error for spacy: 14910.399978536167
